In [352]:
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from collections import OrderedDict, Counter
from itertools import product, groupby, chain
from collections import defaultdict, Iterable
from operator import itemgetter
import string

# let pandas dataframes show all columns
pd.set_option('display.max_columns', None)

# flatten sublists
def flatten(l):
    for el in l:
        if isinstance(el, Iterable) and not isinstance(el, (str, bytes)):
            yield from flatten(el)
        else:
            yield el


# --load semantic types
sem_type = []
with open('/Users/luyu/Documents/Fall 2019/Independent Research/Pregnancy_Yahoo/umls/map/Diabetes related semantic types.txt') as st:
    for s in st:
        #print(s.split('|'))
        sem_type.append(s.split('|')[-1].replace('\n', ''))
sem_type = [s for s in sem_type if s != '']

# load metamap results
#data = pd.read_csv("/Users/luyu/Documents/Fall 2019/Independent Research/ECIR 2020/query_questions_metamap1.csv")
data = pd.read_csv("/Users/luyu/Documents/Fall 2019/Independent Research/ECIR 2020/diabetes_metamap1.csv")
data = data.values.tolist()
data = [[d[1], d[2]] for d in data]
ID = [d[0] for d in data]
metamap = [d[1] for d in data]
# define noise caused by stop words
noise = ['AM', 'I- (Iodides) ', 'I NOS (Blood group antibody I) ', 'M-16', 'M NOS (M NOS ANTIBODY) ','N NOS', 'N+', 'N+ (tumor staging)',
         'M+', 'M+ (tumor staging)', 'MY (Malaysia) ','Do', 'TO', 'IS (Israel)', 'IS (Immunogenicity Specimen Assessments Domain) ']
metamap = [str(m) for m in metamap]
metamap = [m.replace('];', '] |') for m in metamap]
metamap = [m.replace(' N C', ' | C') for m in metamap]
metamap = [m.replace('  ;    ', '') for m in metamap]
metamap = [m.replace(' nan ', '') for m in metamap]
metamap = [m.split('|') for m in metamap]
metamap = [[mm.lstrip() for mm in m] for m in metamap]
# remove CUIs caused by stop words
for f in metamap:
    for ff in list(f):
        for n in noise:
            if n in ff:
                f.remove(ff)
                ff = ''
# remove CUIs with score < 600
metamap = [[ff for ff in f if ff[:4].strip().isdigit() == True and int(ff[:4]) >= 600] for f in metamap]
#for m in metamap:print(m)
ID_metamap = zip(ID, metamap)

# load question pool
pool = pd.read_csv("/Users/luyu/Documents/Master Thesis/Question_Pool.csv", header=None)
pool = [[p[0], p[1]] for p in pool.values.tolist()]
id_Q = []
ID_Q = []
for x in product(pool, ID):
    if int(x[0][0]) == int(x[1]) and x[0] not in id_Q:id_Q.append(x[0])
for x in product(ID, id_Q):
    if int(x[0]) == int(x[1][0]): ID_Q.append(x[1])
#for i in zip(ID, ID_Q):print(i)
#for i in ID_Q:print(i)

# semantic type filtering
#for s in sem_type:
#    filtered = [[mm for mm in m if s.lower() in mm.lower()] for m in metamap]
#filt = [f for f in filtered if f != []]
filtered =[]
for x in product(sem_type, ID_metamap):
    if x[0].lower() in str(x[1][1]).lower() and x[1] not in filtered:
        filtered.append(x[1])
mu = []
for f in filtered:
    for s in sem_type:
        if [ff for ff in f[1] if s in ff] != [] and [ff for ff in f[1] if s in ff] not in mu:
            #print([f[0], [ff for ff in f[1] if s in ff]])
            mu.append([f[0], [ff for ff in f[1] if s in ff]])

In [34]:
#print(len(mu))

8411


In [225]:
ID_metamap = zip(ID, metamap)
fin = []
for x, y in product(ID_metamap, mu):
    #print(x[1] in x[0][1], flush=True)
    if int(x[0]) == int(y[0]):
        fin.append(y)
        #print(x, y, flush=True)

In [226]:
#for f in fin:print(f)
ffin = []
for f in fin:
    if f not in ffin:
        ffin.append(f)
#for f in ffin:print(f)

[2247438, ['923   C2585282:Blood glucose concentration [Finding] ']]
[2247438, ['645   C0455280:plasma glucose (Plasma glucose result) [Laboratory or Test Result] ']]
[2881748, ['670   C1447490:EAT-2 (SH2D1B protein;  human) [Amino Acid;  Peptide;  or Protein; Biologically Active Substance] ']]
[3663888, ['626   C4291676:A1C (A1C -- test) [Diagnostic Procedure] ']]
[3808799, ['888   C0004076:Glucose - urine test (Glucose measurement;  urine) [Laboratory Procedure] ']]
[83397, ['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ', '901   C0007012:CARBON DIOXIDE (Carbon Dioxide) [Biologically Active Substance; Inorganic Chemical] ']]
[83397, ['901   C0007012:CARBON DIOXIDE (Carbon Dioxide) [Biologically Active Substance; Inorganic Chemical] ']]
[83397, ['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ']]
[3079780, ['1000   C3843708:29+ [Finding] ']]
[3079780, ['791   C02

[2759088, ['1000   C0011849:Diabetes (Diabetes Mellitus) [Disease or Syndrome] ', '1000   C0011854:Type I Diabetes (Diabetes Mellitus;  Insulin-Dependent) [Disease or Syndrome] ']]
[2759088, ['861   C0332575:Red (Redness) [Finding] ']]
[2759088, ['1000   C0235267:red eyes (Redness of eye) [Sign or Symptom] ']]
[3031547, ['799   C0002059:ALKALINE PHOSPHATASE (Alkaline Phosphatase) [Amino Acid;  Peptide;  or Protein; Enzyme] ']]
[3031547, ['807   C0553702:high calcium (ca increase) [Finding] ', '799   C0860866:potassium low [Finding] ']]
[3031547, ['840   C0018941:Blood Test (Hematologic Tests) [Laboratory Procedure] ']]
[2069142, ['645   C2698559:Breakfast [Daily or Recreational Activity] ']]
[239626, ['626   C0242209:SUGAR (Sugars) [Organic Chemical; Pharmacologic Substance] ']]
[239626, ['827   C0359520:Cornflour (Corn flour - dietary) [Food] ', '812   C0359520:Cornflour (Corn flour - dietary) [Food] ']]
[239626, ['632   C0013470:Eat (Eating) [Organism Function] ']]
[1767108, ['1000  

[2206355, ['637   C0723893:TriCor (Tricor) [Organic Chemical; Pharmacologic Substance] ', '629   C0723893:TriCor (Tricor) [Organic Chemical; Pharmacologic Substance] ']]
[1020578, ['1000   C0085207:Gestational Diabetes [Disease or Syndrome] ']]
[1020578, ['827   C0453577:Pizza [Food] ']]
[1020578, ['1000   C1519355:Slice [Substance] ']]
[3685084, ['812   C2698559:Breakfast [Daily or Recreational Activity] ']]
[3685084, ['1000   C0681578:junk food [Food] ']]
[3685084, ['645   C0013470:Eat (Eating) [Organism Function] ']]
[1330194, ['626   C0007004:CARBOHYDRATE (Carbohydrates) [Organic Chemical] ', '812   C0005802:Blood Sugar (Blood Glucose) [Organic Chemical] ', '861   C0007004:CARBOHYDRATE (Carbohydrates) [Organic Chemical] ', '1000   C0005802:Blood Sugar (Blood Glucose) [Organic Chemical] ']]
[675240, ['666   C0428568:Fasting blood glucose level (Fasting blood glucose measurement) [Laboratory Procedure] ']]
[3440269, ['632   C1995000:Back;  NOS (Back structure;  excluding neck) [Body 

[1827684, ['827   C0011847:Diabetes [Disease or Syndrome] ', '1000   C0011847:Diabetes [Disease or Syndrome] ']]
[1827684, ['827   C0311392:SIGNS (Physical findings) [Finding] ']]
[1827684, ['660   C1457887:Symptom (Symptoms) [Sign or Symptom] ']]
[607540, ['812   C0011847:Diabetes [Disease or Syndrome] ', '812   C0011847:Diabetes [Disease or Syndrome] ']]
[2488340, ['1000   C2349986:Digestion (Protein Digestion (research activity)) [Research Activity] ']]
[3079266, ['827   C0015450:FACE (Face) [Body Location or Region] ', '1000   C0446516:Arms (Upper arm) [Body Location or Region] ']]
[3079266, ['827   C0011849:Diabetes (Diabetes Mellitus) [Disease or Syndrome] ']]
[3478224, ['1000   C1709305:Happen (Occur (action)) [Activity] ']]
[3478224, ['645   C1533581:INSULIN (Recombinant Insulin) [Amino Acid;  Peptide;  or Protein; Hormone; Pharmacologic Substance] ']]
[1551465, ['861   C1998602:Meal (Meal (occasion for eating)) [Daily or Recreational Activity] ']]
[1551465, ['812   C0016452:FO

[15154, ['1000   C0038636:SUCROSE (Sucrose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ', '902   C0026492:Simple Carbohydrate (Monosaccharides) [Organic Chemical] ', '861   C0556154:Complex carbohydrate [Organic Chemical] ']]
[93334, ['861   C0011849:Diabetes (Diabetes Mellitus) [Disease or Syndrome] ']]
[93334, ['1000   C0311392:Sign (Physical findings) [Finding] ']]
[93334, ['708   C0235150:Feeling Cold [Sign or Symptom] ']]
[93334, ['827   C1710386:Thermostat (Thermostat Device) [Manufactured Object] ']]
[1822742, ['795   C0242209:SUGAR (Sugars) [Organic Chemical; Pharmacologic Substance] ']]
[1822742, ['651   C0561296:cut back (Cut of back) [Injury or Poisoning] ']]
[28904, ['1000   C0011854:Type I Diabetes (Diabetes Mellitus;  Insulin-Dependent) [Disease or Syndrome] ']]
[28904, ['1000   C1148523:Born (Childbirth) [Organism Function] ']]
[805239, ['861   C0033268:Production (production) [Occupational Activity] ']]
[805239, ['694   C1533581:INSULIN (

In [209]:
fina = []
for k, g in groupby(ffin, itemgetter(0)):
    group = list(g)
    if len(group) == 1:
        fina.append(group[0])
    else:
        fina.append([k, [sub[1] for sub in group]])

for f in fina:print(f)

[2247438, [['923   C2585282:Blood glucose concentration [Finding] '], ['645   C0455280:plasma glucose (Plasma glucose result) [Laboratory or Test Result] ']]]
[2881748, ['670   C1447490:EAT-2 (SH2D1B protein;  human) [Amino Acid;  Peptide;  or Protein; Biologically Active Substance] ']]
[3663888, ['626   C4291676:A1C (A1C -- test) [Diagnostic Procedure] ']]
[3808799, ['888   C0004076:Glucose - urine test (Glucose measurement;  urine) [Laboratory Procedure] ']]
[83397, [['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ', '901   C0007012:CARBON DIOXIDE (Carbon Dioxide) [Biologically Active Substance; Inorganic Chemical] '], ['901   C0007012:CARBON DIOXIDE (Carbon Dioxide) [Biologically Active Substance; Inorganic Chemical] '], ['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ']]]
[3079780, [['1000   C3843708:29+ [Finding] '], ['791   C0205307:NORMAL (Normal) [Qualitat

[2761323, ['861   C0005802:Blood Sugar (Blood Glucose) [Organic Chemical] ']]
[1886862, ['804   C1305866:weight (Weighing patient) [Health Care Activity] ', '861   C1305866:weight (Weighing patient) [Health Care Activity] ']]
[610715, ['1000   C0011882:DIABETIC NEUROPATHY (Diabetic Neuropathies) [Disease or Syndrome] ', '1000   C0011860:Type II Diabetes (Diabetes Mellitus;  Non-Insulin-Dependent) [Disease or Syndrome] ']]
[955902, [['1000   C0005802:Blood Sugar (Blood Glucose) [Organic Chemical] '], ['1000   C0310255:SURVIVE (survive) [Pharmacologic Substance] ', '1000   C0018880:He (Helium) [Element;  Ion;  or Isotope; Pharmacologic Substance] ']]]
[249265, [['1000   C0011860:Type II Diabetes (Diabetes Mellitus;  Non-Insulin-Dependent) [Disease or Syndrome] '], ['1000   C0012155:Diet [Food] '], ['827   C0085732:Able (Ability) [Organism Attribute] '], ['1000   C1522704:Exercise (Exercise Pain Management) [Therapeutic or Preventive Procedure] ']]]
[633089, [['632   C2825972:Cant [Findin

[1153010, [['827   C0011849:Diabetes (Diabetes Mellitus) [Disease or Syndrome] ', '1000   C0038454:Strokes (Cerebrovascular accident) [Disease or Syndrome] '], ['1000   C2926615:High blood pressure (Ever told by doctor or nurse that you have high blood pressure:Finding:Point in time:^Patient:Ordinal) [Clinical Attribute] ']]]
[2173176, [['1000   C1533128:Patch (Body tissue patch material) [Biomedical or Dental Material] '], ['861   C0011847:Diabetes [Disease or Syndrome] '], ['793   C1706353:Crack [Finding] ', '1000   C0311392:Sign (Physical findings) [Finding] '], ['660   C0011682:DRYING (Desiccation) [Natural Phenomenon or Process] ']]]
[2393203, [['861   C0242209:SUGAR (Sugars) [Organic Chemical; Pharmacologic Substance] '], ['694   C0013470:Eating [Organism Function] '], ['1000   C1322279:Dilate (Dilate procedure) [Therapeutic or Preventive Procedure] ']]]
[3516149, [['645   C0875954:Actos [Organic Chemical; Pharmacologic Substance] '], ['1000   C0031843:function (physiological asp

In [81]:
eid = [f[0] for f in fina]
nil = [[i, []] for i in ID if i not in eid]
#print(nil)
#print(len(nil)) # 171
#print(len(fina)) # 2827
#print(len(fina) + len(nil)) # 2998
#for n in nil:print(n)

[870275, []]
[2759041, []]
[3760599, []]
[1692067, []]
[3563637, []]
[1966605, []]
[1586266, []]
[214123, []]
[1598800, []]
[505238, []]
[1648297, []]
[86746, []]
[3765928, []]
[1940308, []]
[1529194, []]
[3698012, []]
[1593679, []]
[1687403, []]
[1763978, []]
[3635027, []]
[778299, []]
[76469, []]
[1240126, []]
[2084659, []]
[460838, []]
[2367538, []]
[177109, []]
[998413, []]
[1623985, []]
[3375599, []]
[865558, []]
[201972, []]
[1708976, []]
[1173488, []]
[741561, []]
[1826049, []]
[734108, []]
[820028, []]
[887282, []]
[2420496, []]
[3770742, []]
[2826413, []]
[3251026, []]
[3751541, []]
[1221979, []]
[1971387, []]
[3671452, []]
[1067721, []]
[360545, []]
[976831, []]
[783517, []]
[3684933, []]
[246851, []]
[1564233, []]
[2303045, []]
[587765, []]
[393694, []]
[2826362, []]
[2518314, []]
[1099001, []]
[229449, []]
[3426850, []]
[1662078, []]
[1667276, []]
[216731, []]
[126402, []]
[76362, []]
[2084661, []]
[906360, []]
[3722945, []]
[578246, []]
[762658, []]
[1082461, []]
[929861, 

In [142]:
finn = fina + nil
#print(len(finn))
#print(len(ID_Q))
for f in finn:print(f)

[2247438, [['923   C2585282:Blood glucose concentration [Finding] '], ['645   C0455280:plasma glucose (Plasma glucose result) [Laboratory or Test Result] ']]]
[2881748, [['670   C1447490:EAT-2 (SH2D1B protein;  human) [Amino Acid;  Peptide;  or Protein; Biologically Active Substance] '], ['670   C1447490:EAT-2 (SH2D1B protein;  human) [Amino Acid;  Peptide;  or Protein; Biologically Active Substance] ']]]
[3663888, ['626   C4291676:A1C (A1C -- test) [Diagnostic Procedure] ']]
[3808799, ['888   C0004076:Glucose - urine test (Glucose measurement;  urine) [Laboratory Procedure] ']]
[83397, [['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ', '901   C0007012:CARBON DIOXIDE (Carbon Dioxide) [Biologically Active Substance; Inorganic Chemical] '], ['901   C0007012:CARBON DIOXIDE (Carbon Dioxide) [Biologically Active Substance; Inorganic Chemical] '], ['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical

[28914, [['1000   C0015689:Omega-3 (Omega-3 Fatty Acids) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['660   C0016157:FISH OIL (Fish Oils) [Organic Chemical; Pharmacologic Substance] ', '1000   C0015689:Omega-3 (Omega-3 Fatty Acids) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['660   C0016157:FISH OIL (Fish Oils) [Organic Chemical; Pharmacologic Substance] ', '1000   C0015689:Omega-3 (Omega-3 Fatty Acids) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['660   C0016157:FISH OIL (Fish Oils) [Organic Chemical; Pharmacologic Substance] ', '1000   C0015689:Omega-3 (Omega-3 Fatty Acids) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ']]]
[2094895, [['649   C0428554:Blood glucose level (Finding of blood glucose level) [Laboratory or Test Result] '], ['694   C0013470:Eating [Organism Function] '], ['649   C0428554:Blood glucose level (Finding of blood glucose level)

[984048, [['827   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['827   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['827   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['1000   C0150312:PRESENT (Present) [Finding] ', '1000   C0150312:In (Present) [Finding] ', '1000   C0438141:normal urine (Urine screening normal) [Finding] '], ['827   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ']]]
[3763977, [['804   C0028912:Ointments [Biomedical or Dental Material] '], ['673   C0036079:SALICYLIC ACID (Salicylic Acid) [Organic Chemical; Pharmacologic Substance] '], ['673   C0036079:SALICYLIC ACID (Salicylic Acid) [Organic Chemical; Pharmacologic Substance] '], ['1000   C0011847:Diabetes [Disease or Syndrome] '], ['673   C0036079:SALICYLIC ACID (Salicylic Acid) [O

In [94]:
id_Q = []
ID_Q = []
for x in product(pool, ID):
    if int(x[0][0]) == int(x[1]) and x[0] not in id_Q:id_Q.append(x[0])
for x in product(ID, id_Q):
    if int(x[0]) == int(x[1][0]): ID_Q.append(x[1])
for i in ID_Q:print(i)

[2247438, 'why plasma glucose is 10 to 15% higher than corresponding whole blood glucose concentration? ']
[2881748, 'i have not eaten in 2 days and my blood sugar levels are 159? are these levels high']
[3663888, 'is an A1c level of 8.0 bad? ']
[3808799, 'I have nill glucose in urine test but my HbA1C is 10?/ How come? ']
[83397, 'My glucose is 120, tryglycerides 95, LDL 128, HDL 53, carbon dioxide 32, what does this mean? ']
[3079780, 'Albumin/Creatinine ratio? Is an Albumin/Creatinine ratio of 0.7 normal? Im female, 29.']
[490298, 'What is Serum Chemistry. My Serum Creatinine shows 1.50MG/DL, what that means & what precaution should be take? ']
[1891547, 'i just had 3 cup water and did my blood sugar level it was 5.3 is this normal for non-diabetic? ']
[670465, 'I had a starbucks an hr before a bloodtest, and my glucose was 230. Should i be worried? ']
[863102, 'Should I celebrate my 6.6 A1c with a cream filled donut or a banana split? ']
[1065217, '108 glucose too high for your sug

[889747, 'Are you aware about diabetes type 1? Do you know everything you can about diabetes? reply with what you know.']
[2758838, 'Is sugar levels consistently over 200 with insulin dangerous ? ']
[988730, 'how to increase 5 kgs in one month? ']
[2555503, 'i have been operated 4 stone in kidney,plz tell me d precautions? ']
[1087651, 'if you are a diabetic would u try this recipe? http://www.cooks.com/rec/view/0,2314,155179-233201,00.html']
[1863498, '1170 mg = how many grams ? ']
[54111, 'whats the difference between type 1 diabetes and type 2? just wondering']
[80083, 'What foods should a 78 yr old male w/ diabetes avoid? ']
[2685502, 'Type 1 diabetes info? How much sugar should a type one diabetic have']
[3215594, 'My level hcg level is 104 is that good? ']
[3530495, 'I have diabetes and take 2 insulin with high blood pressure. do i qualify for disability.? ']
[2076680, 'Blood sugar of 131 is that a good number? Just got these results today.']
[625723, 'what is type 2 diabetis? ']

[3687425, 'Is Arbor Mist ok for a DIABETIC to drink? ']
[422910, 'Anybody know what is the conductivity of glucose and sucrose? ']
[3478239, 'is lisinopril a blood thiner? ']
[1087657, 'can i take amitriptyline with epilim? i have just been told i have fibromyalgia can i take amitriptyline with epilim.']
[1943697, 'Is a A1C blood level considered prediabetic? ']
[3515983, 'which function is associtaed with phagocytes in the blood? a.transporting dissolved nutrientsb.producing hormonesc.engulfing bacteriad.initiating blood cells']
[311255, 'when did the DSi come out? ']
[1255639, 'I tripped and hurt my knee today. is it true that oxygen will get in and give me diabetes? ']
[592804, 'Is diabetes curable? If yes what % of patients get cured & howmany have been cured in India till now? ']
[2758577, 'how can I safely gain weight as a diabetic? ']
[1137088, 'Could blood thinners affect a BAC level, like Coumadin? ']
[2685275, 'Losing hair from blood thinner, diabetes, heart problem what do I

In [110]:
final = []
for x in product(ID_Q, finn):
    if x[0][0] == x[1][0] and [x[0][0], x[0][1], x[1][1]] not in final:
        final.append([x[0][0], x[0][1], x[1][1]])
#for f in final:print(f)
#print(len(final)) # 2990

[2247438, 'why plasma glucose is 10 to 15% higher than corresponding whole blood glucose concentration? ', [['923   C2585282:Blood glucose concentration [Finding] '], ['645   C0455280:plasma glucose (Plasma glucose result) [Laboratory or Test Result] ']]]
[2881748, 'i have not eaten in 2 days and my blood sugar levels are 159? are these levels high', [['670   C1447490:EAT-2 (SH2D1B protein;  human) [Amino Acid;  Peptide;  or Protein; Biologically Active Substance] '], ['670   C1447490:EAT-2 (SH2D1B protein;  human) [Amino Acid;  Peptide;  or Protein; Biologically Active Substance] ']]]
[3663888, 'is an A1c level of 8.0 bad? ', ['626   C4291676:A1C (A1C -- test) [Diagnostic Procedure] ']]
[3808799, 'I have nill glucose in urine test but my HbA1C is 10?/ How come? ', ['888   C0004076:Glucose - urine test (Glucose measurement;  urine) [Laboratory Procedure] ']]
[83397, 'My glucose is 120, tryglycerides 95, LDL 128, HDL 53, carbon dioxide 32, what does this mean? ', [['812   C0017725:GLUCO

[134547, 'Can someone who isnt diabetic still get high blood sugars (over 120)? ', [['845   C0020456:HIGH blood sugars (Hyperglycemia) [Disease or Syndrome] '], ['629   C0241863:DIABETIC (diabetic) [Finding] ']]]
[3478271, 'What are the symptons for type 1 children diabetes!?!? ', ['923   C0011854:Type 1 Diabetes (Diabetes Mellitus;  Insulin-Dependent) [Disease or Syndrome] ']]
[257033, 'does having type 2 diabetes affect your sex drive? ', [['1000   C0011860:Type II Diabetes (Diabetes Mellitus;  Non-Insulin-Dependent) [Disease or Syndrome] '], ['1000   C0001721:Affect (Affect (mental function)) [Mental Process] ', '1000   C0023618:Sex Drive (Libido) [Mental Process] ']]]
[573234, 'what is type 1 and 2 diabetes? please explain type 1 and 2 diabetes?', ['861   C0011849:Diabetes (Diabetes Mellitus) [Disease or Syndrome] ', '861   C0011849:Diabetes (Diabetes Mellitus) [Disease or Syndrome] ']]
[1504955, 'what is 20% off $244? ', []]
[308576, 'Iam taking Mixtard insulin for one month. Morn

[1113847, 'What is the experience with collagen peptide in cases of osteoarthritis. Claims are being made as usual.? ', [['632   C0009325:Collagen [Amino Acid;  Peptide;  or Protein; Pharmacologic Substance] ', '632   C0030956:Peptide (Peptides) [Amino Acid;  Peptide;  or Protein; Pharmacologic Substance] '], ['799   C0029408:OSTEOARTHRITIS (Degenerative polyarthritis) [Disease or Syndrome] '], ['632   C0009325:Collagen [Amino Acid;  Peptide;  or Protein; Pharmacologic Substance] ', '632   C0030956:Peptide (Peptides) [Amino Acid;  Peptide;  or Protein; Pharmacologic Substance] '], ['1000   C0237607:experience (Practice Experience) [Mental Process] ']]]
[3684867, 'What is the IUPAC Name of glucose? ', [['861   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['861   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['861   C0017725:GLUCOSE (Glucose) [Biologically Active Subst

In [238]:
ult = []
for f in final:
    #print([f[0], f[1], list(set(list(flatten(f[2]))))])
    ult.append([f[0], f[1], list(set(list(flatten(f[2]))))])
#print(len(ult)) # 2990
for u in ult:print(u)

[2247438, 'why plasma glucose is 10 to 15% higher than corresponding whole blood glucose concentration? ', ['923   C2585282:Blood glucose concentration [Finding] ', '645   C0455280:plasma glucose (Plasma glucose result) [Laboratory or Test Result] ']]
[2881748, 'i have not eaten in 2 days and my blood sugar levels are 159? are these levels high', ['670   C1447490:EAT-2 (SH2D1B protein;  human) [Amino Acid;  Peptide;  or Protein; Biologically Active Substance] ']]
[3663888, 'is an A1c level of 8.0 bad? ', ['626   C4291676:A1C (A1C -- test) [Diagnostic Procedure] ']]
[3808799, 'I have nill glucose in urine test but my HbA1C is 10?/ How come? ', ['888   C0004076:Glucose - urine test (Glucose measurement;  urine) [Laboratory Procedure] ']]
[83397, 'My glucose is 120, tryglycerides 95, LDL 128, HDL 53, carbon dioxide 32, what does this mean? ', ['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ', '901   C0007012:CARBON DIOXIDE (Car

[28929, 'Is yogurt good for diabetics? ', ['1000   C0241863:diabetics (diabetic) [Finding] ', '660   C0043419:Yogurt [Food] ']]
[126442, 'diabetic foot pain and numness? ', ['734   C0206172:Diabetic Foot [Disease or Syndrome] ', '660   C0241863:DIABETIC (diabetic) [Finding] ', '901   C0016512:FOOT PAIN (Foot pain) [Sign or Symptom] ', '827   C1962977:Pain NOS (Pain NOS;  CTCAE) [Finding] ']]
[2759065, 'Im diabetic is it safe for me to get a tatoo? ', ['637   C0241863:DIABETIC (diabetic) [Finding] ', '804   C1366940:Tattoo [Finding] ']]
[3659080, 'explain how our body reacts to hyperglycemia and hypoglycemia in order to get a normal glucose level? ', ['827   C1268086:Body (Body structure) [Anatomical Structure] ', '861   C0522082:Normal glucose level [Finding] ', '861   C0020456:HYPERGLYCEMIA (Hyperglycemia) [Disease or Syndrome] ', '694   C0020615:HYPOGLYCEMIA (Hypoglycemia) [Disease or Syndrome] ', '1000   C4224854:React [Hormone; Organic Chemical; Pharmacologic Substance] ']]
[353043

[1240140, 'what is a NEU # Blood test? ', ['840   C0018941:Blood Test (Hematologic Tests) [Laboratory Procedure] ', '637   C1702024:NEU (ERBB2 protein;  human) [Amino Acid;  Peptide;  or Protein; Enzyme; Receptor] ']]
[3215911, 'WHat are the side-effects of eating sugar based foods more.? ', ['822   C0453802:Sugar foods (Carbohydrate food) [Food] ', '793   C0013470:Eating [Organism Function] ']]
[3515775, 'Is being diagnosed with diabeties a big life-threatening deal? I am so scared.', ['1000   C0015726:Scared (Fear (Mental Process)) [Mental Process] ', '660   C1546953:Life threatening (Life threatening - Event Consequence) [Idea or Concept] ', '1000   C0011900:Diagnosed (Diagnosis) [Diagnostic Procedure] ']]
[2239403, 'Why do my baby has high CRP level in blood? ', ['646   C4321237:High Level [Finding] ', '790   C0005768:BLOOD (In Blood) [Body Substance] ', '623   C3890735:CRp (Complete Response with Incomplete Platelet Recovery) [Finding] ']]
[2327849, 'is feet swelling a symptom of 

In [240]:
df = pd.DataFrame(ult, columns=['id', 'question', 'metamap_result'], index=None)
#df.head()

id                                           question  \
0  2247438  why plasma glucose is 10 to 15% higher than co...   
1  2881748  i have not eaten in 2 days and my blood sugar ...   
2  3663888                       is an A1c level of 8.0 bad?    
3  3808799  I have nill glucose in urine test but my HbA1C...   
4    83397  My glucose is 120, tryglycerides 95, LDL 128, ...   

                                      metamap_result  
0  [923   C2585282:Blood glucose concentration [F...  
1  [670   C1447490:EAT-2 (SH2D1B protein;  human)...  
2  [626   C4291676:A1C (A1C -- test) [Diagnostic ...  
3  [888   C0004076:Glucose - urine test (Glucose ...  
4  [812   C0017725:GLUCOSE (Glucose) [Biologicall...

In [241]:
df.to_csv("/Users/luyu/Documents/Fall 2019/Independent Research/ECIR 2020/test.csv")

In [135]:
#df.iloc[-1]

id                                                          1702248
question          Is there a way to check myself to see if I hav...
metamap_result    [[1000   C1283174:Check (Checking (action)) [A...
Name: 2989, dtype: object

In [100]:
#import collections
#print([item for item, count in collections.Counter(ID).items() if count > 1])

[1206724, 2303014, 3127071, 1912588, 3251157, 3455144, 415038, 1035411, 102910, 3290485]


In [130]:
qual = pd.read_csv("/Users/luyu/Documents/Fall 2019/Independent Research/ECIR 2020/question_qualifiedCUI.csv")
quali = [q[3] for q in qual.values.tolist()]
ql = [q for q in quali if len(q) > 2]
nq = [q for q in quali if len(q) == 2]
#print(len(nq)) # 163
#print(len(ql)) # 2827
#print(len(quali) - len(nq)) # 2827
#for q in quali:print(len(q))

2827


In [204]:
for f in fina:
    print(list(k for k,_ in groupby(f[1])))
    #print(list(k for k,_ in groupby(f[2])))

[['923   C2585282:Blood glucose concentration [Finding] '], ['645   C0455280:plasma glucose (Plasma glucose result) [Laboratory or Test Result] ']]
[['670   C1447490:EAT-2 (SH2D1B protein;  human) [Amino Acid;  Peptide;  or Protein; Biologically Active Substance] ']]
['626   C4291676:A1C (A1C -- test) [Diagnostic Procedure] ']
['888   C0004076:Glucose - urine test (Glucose measurement;  urine) [Laboratory Procedure] ']
[['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ', '901   C0007012:CARBON DIOXIDE (Carbon Dioxide) [Biologically Active Substance; Inorganic Chemical] '], ['901   C0007012:CARBON DIOXIDE (Carbon Dioxide) [Biologically Active Substance; Inorganic Chemical] '], ['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] '], ['812   C0017725:GLUCOSE (Glucose) [Biologically Active Substance; Organic Chemical; Pharmacologic Substance] ', '901   C0007012:CARBON DIOX

[['1000   C0241863:diabetics (diabetic) [Finding] '], ['1000   C4291676:A1C (A1C -- test) [Diagnostic Procedure] ']]
[['629   C2346927:Mg++ (Magnesium Cation) [Element;  Ion;  or Isotope; Pharmacologic Substance] '], ['829   C0573204:Caffeine overdose [Injury or Poisoning] '], ['629   C2346927:Mg++ (Magnesium Cation) [Element;  Ion;  or Isotope; Pharmacologic Substance] ']]
[['1000   C0025598:METFORMIN (Metformin) [Organic Chemical; Pharmacologic Substance] ']]
['1000   C2986560:Best Answer (Best Overall Response) [Finding] ']
[['861   C0034754:Reading (Reading (activity)) [Daily or Recreational Activity] '], ['818   C0005802:Blood Sugar (Blood Glucose) [Organic Chemical] '], ['861   C0018880:He (Helium) [Element;  Ion;  or Isotope; Pharmacologic Substance] '], ['1000   C0241863:DIABETIC (diabetic) [Finding] '], ['861   C0018880:He (Helium) [Element;  Ion;  or Isotope; Pharmacologic Substance] ']]
['1000   C0011849:Diabetes (Diabetes Mellitus) [Disease or Syndrome] ']
[['1000   C000196

[['1000   C0237886:sorts (Sorting (Cognition)) [Mental Process] '], ['844   C0030275:pancreas transplant (Pancreas Transplantation) [Therapeutic or Preventive Procedure] ']]
[['827   C0019932:Hormones [Hormone] '], ['1000   C0428554:blood sugar levels (Finding of blood glucose level) [Laboratory or Test Result] '], ['1000   C1550141:Control (control substance) [Substance] '], ['1000   C0428554:blood sugar levels (Finding of blood glucose level) [Laboratory or Test Result] ']]
['804   C0011847:Diabetes [Disease or Syndrome] ']
[['660   C1874451:BASIS (Basis) [Pharmacologic Substance] '], ['1000   C1262477:WEIGHTLOSS (Weight decreased) [Finding] ', '1000   C2911645:Weight loss (Weight Loss;  CTCAE) [Finding] ', '861   C1262477:WEIGHTLOSS (Weight decreased) [Finding] ', '861   C2911645:Weight loss (Weight Loss;  CTCAE) [Finding] '], ['660   C1874451:BASIS (Basis) [Pharmacologic Substance] ']]
['827   C0029456:OSTEOPOROSIS (Osteoporosis) [Disease or Syndrome] ']
[['637   C1702024:NEU (ERBB

In [320]:
# extract CUIs
qid = [i[0] for i in ult]
ccpc = [i[2] for i in ult]
cui = [[mm[4:15].replace(':', '').lstrip() for mm in m] for m in ccpc]
for c in cui:
    for cc in c:
        if '155179' in cc:
            c.remove(cc)
cps = [' '.join(c) for c in cui]
qid_cui = zip(qid, cui)
#for c in cps:print(c)

# --- vectorize CUIs ---
vectorizer = TfidfVectorizer(min_df=5)
C = vectorizer.fit_transform(cps)
doc_term_matrix = C.todense()
ma = pd.DataFrame(doc_term_matrix, columns=vectorizer.get_feature_names(),index=qid)
# compute cosin_similarity
out = cosine_similarity(ma, ma)
#print(out)
output = pd.DataFrame(out, index=qid, columns=qid)
print(output.head())

         2247438  2881748  3663888  3808799  83397    3079780  490298   \
2247438      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
2881748      0.0      1.0      0.0      0.0      0.0      0.0      0.0   
3663888      0.0      0.0      1.0      0.0      0.0      0.0      0.0   
3808799      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
83397        0.0      0.0      0.0      0.0      1.0      0.0      0.0   

         1891547   670465   863102   1065217  2367457  1330863  1856600  \
2247438      0.0  0.000000      0.0      0.0      0.0      0.0      0.0   
2881748      0.0  0.000000      0.0      0.0      0.0      0.0      0.0   
3663888      0.0  0.000000      1.0      0.0      0.0      0.0      0.0   
3808799      0.0  0.000000      0.0      0.0      0.0      0.0      0.0   
83397        0.0  0.584753      0.0      0.0      0.0      0.0      0.0   

         590290   2555099  3779970   713903   3478300  1206724   790946   \
2247438      0.0      0.0   

In [312]:
count_vectorizer = CountVectorizer(stop_words='english')
count_vectorizer = CountVectorizer()
sparse_matrix = count_vectorizer.fit_transform(cps)
doc_term_matrix = sparse_matrix.todense()
dd = pd.DataFrame(doc_term_matrix, 
                  columns=count_vectorizer.get_feature_names(), 
                  index=qid)
dd.head()

c0000598  c0000833  c0000889  c0000912  c0000921  c0000925  c0001645  \
2247438         0         0         0         0         0         0         0   
2881748         0         0         0         0         0         0         0   
3663888         0         0         0         0         0         0         0   
3808799         0         0         0         0         0         0         0   
83397           0         0         0         0         0         0         0   

         c0001721  c0001779  c0001861  c0001924  c0001948  c0001962  c0001967  \
2247438         0         0         0         0         0         0         0   
2881748         0         0         0         0         0         0         0   
3663888         0         0         0         0         0         0         0   
3808799         0         0         0         0         0         0         0   
83397           0         0         0         0         0         0         0   

         c0001975  c0002006  c0002059  c0002170  c0002422  c0002424  c0002645  \
2247438         0         0         0         0         0         0         0   
2881748         0         0         0         0         0         0         0   
3663888         0         0         0         0         0         0         0   
3808799         0         0         0         0         0         0         0   
83397           0         0         0         0         0         0         0   

         c0002688  c0002845  c0002871  c0003009  c0003086  c0003123  c0003237  \
2247438         0         0         0         0         0         0         0   
2881748         0         0         0         0         0         0         0   
3663888         0         0         0         0         0         0         0   
3808799         0         0         0         0         0         0         0   
83397           0         0         0         0         0         0         0   

         c0003241  c0003280  c0003289  c0003320  c0003364  c0003467  c0003811  \
2247438         0         0         0         0         0         0         0   
2881748         0         0         0         0         0         0         0   
3663888         0         0         0         0         0         0         0   
3808799         0         0         0         0         0         0         0   
83397           0         0         0         0         0         0         0   

         c0003920  c0003962  c0004057  c0004076  c0004135  c0004271  c0004381  \
2247438         0         0         0         0         0         0         0   
2881748         0         0         0         0         0         0         0   
3663888         0         0         0         0         0         0         0   
3808799         0         0         0         1         0         0         0   
83397           0         0         0         0         0         0         0   

         c0004388  c0004448  c0004454  c0004600  c0004722  c0004896  c0004916  \
2247438         0         0         0         0         0         0         0   
2881748         0         0         0         0         0         0         0   
3663888         0         0         0         0         0         0         0   
3808799         0         0         0         0         0         0         0   
83397           0         0         0         0         0         0         0   

         c0004922  c0004927  c0005135  c0005329  c0005382  c0005388  c0005437  \
2247438         0         0         0         0         0         0         0   
2881748         0         0         0         0         0         0         0   
3663888         0         0         0         0         0         0         0   
3808799         0         0         0         0         0         0         0   
83397           0         0         0         0         0         0         0   

         c0005575  c0005615  c0005767  c0005768  c0005770  c0005775  c0005802  \
2247438         0         0     

In [334]:
# --- select columns that are query questions ---
# 1) load query questions
# load query questions
query = pd.read_csv("/Users/luyu/Documents/Fall 2019/Independent Research/ECIR 2020/query_questions.csv", encoding='utf-8')
q_id = [int(q) for q in query['q_id'].tolist()]
query = [str([q[0], q[1]]) for q in query.values.tolist()]
target = output[q_id]
# define column names and indices
sp = [str([u[0], u[1]]) for u in ult]
target.columns = query
target.index = sp
print(target.head())
target.to_csv("/Users/luyu/Documents/Fall 2019/Independent Research/ECIR 2020/test.csv")

                                                    [836896, 'is 80 a normal glucose reading? ']  \
[2247438, 'why plasma glucose is 10 to 15% high...                                           0.0   
[2881748, 'i have not eaten in 2 days and my bl...                                           0.0   
[3663888, 'is an A1c level of 8.0 bad? ']                                                    0.0   
[3808799, 'I have nill glucose in urine test bu...                                           0.0   
[83397, 'My glucose is 120, tryglycerides 95, L...                                           0.0   

                                                    [83397, 'My glucose is 120, tryglycerides 95, LDL 128, HDL 53, carbon dioxide 32, what does this mean? ']  \
[2247438, 'why plasma glucose is 10 to 15% high...                                                0.0                                                           
[2881748, 'i have not eaten in 2 days and my bl...                           

In [330]:
sp = [[u[0], u[1]] for u in ult]
for q in query:print(q)

[836896, 'is 80 a normal glucose reading? ']
[83397, 'My glucose is 120, tryglycerides 95, LDL 128, HDL 53, carbon dioxide 32, what does this mean? ']
[1891547, 'i just had 3 cup water and did my blood sugar level it was 5.3 is this normal for non-diabetic? ']
[2367457, 'My Nan has a blood sugar level of 2 I know this is bad (but how bad?)? thanks']
[1856600, "Fasting blood sugar is 130. am i diabetic? I'm 30 years old female"]
[2555099, 'fasting blood sugar question? if someone has a fasting blood sugar of 5.7( 105) is that highh??']
[3779970, 'my 5 year old child fasting blood sugar is 110mg/dl ,How it is normal or she want to medicine,? ']
[216699, 'after full food 2 hours later my random blood sugar level is 97.4 whether i am diabetic or not ? ']
[2882318, 'how do you interpret a Fasting Plasma Glucose level of 6.2 mmol/l ? ']
[430242, 'my 13 year olds blood sugar Level first thing in the morning before eating was 120 is this ok? ']
[3663888, 'is an A1c level of 8.0 bad? ']
[865543